### Imports

In [13]:
import pandas as pd
from sklearn.model_selection import train_test_split


### Configuration

In [14]:
EXPERIMENT = "tara"
MODE = "test"
ACTIVITIES = ["relaxing", "eating", "walking", "studying"]

### Dataset

In [15]:
dataset: pd.DataFrame = pd.read_csv(f"state/{EXPERIMENT}_{MODE}_interpolated.csv")
dataset

accel_z   accel_y   accel_x    gyro_z    gyro_y    gyro_x  gravity_z  \
0    -0.023840  0.018390  0.008858 -0.054503 -0.005479  0.011691  -7.563114   
1     0.002951  0.022089 -0.041490 -0.070068  0.088273 -0.000520  -7.004715   
2     0.083199 -0.117540  0.250466  0.099236 -0.050622 -0.041580  -7.546371   
3    -0.024142 -0.041310 -0.124078  0.268303  0.292325  0.254841  -7.262949   
4    -0.343633  0.325876  0.097991 -0.121707 -0.284418 -0.060837  -6.545389   
...        ...       ...       ...       ...       ...       ...        ...   
3540 -0.027468 -0.002052 -0.012776  0.062467  0.000044 -0.000010  -9.806233   
3541 -0.029051  0.008580  0.018632  0.031754 -0.000316 -0.000033  -9.806149   
3542 -0.028269  0.002606  0.002662 -0.000234 -0.000159  0.000208  -9.806189   
3543 -0.028832  0.002296  0.002630  0.023920  0.000002 -0.000178  -9.806191   
3544 -0.028814  0.002313 -0.000165 -0.000034 -0.000017  0.000023  -9.806191   

      gravity_y  gravity_x    ori_qz  ...  bar_relativeAltitude  bar_pressure  \
0     -5.831582  -2.216261  0.663099  ...              0.015858   1018.030701   
1     -6.675822  -1.343320  0.653123  ...              0.026424   1018.029251   
2     -6.011996  -1.740925  0.642579  ...              0.022198   1018.027916   
3     -6.160909  -2.257083  0.731410  ...              0.065531   1018.026657   
4     -6.867339  -2.387059  0.749090  ...              0.122605   1018.028030   
...         ...        ...       ...  ...                   ...           ...   
3540   0.083322   0.035022 -0.157359  ...              5.814162   1017.307434   
3541   0.079065   0.040456 -0.117536  ...              6.261243   1017.307434   
3542   0.082902   0.039185 -0.113216  ...              6.271812   1017.306366   
3543   0.083961   0.039061 -0.108622  ...              6.271812   1017.298370   
3544   0.083584   0.041470 -0.098873  ...              6.271812   1017.298370   

      gps_altitude  gps_latitude  gps_longitude  \
0        40.507936     52.047900       4.382954   
1        40.643834     52.047898       4.382956   
2        40.755786     52.047895       4.382956   
3        40.815552     52.047892       4.382956   
4        40.865129     52.047893       4.382956   
...            ...           ...            ...   
3540     41.526821     52.045305       4.384527   
3541     41.526821     52.045305       4.384527   
3542     41.526821     52.045305       4.384527   
3543     41.526821     52.045305       4.384527   
3544     41.526821     52.045305       4.384527   

                               time  walking  relaxing  eating  studying  
0     2023-06-16 15:39:53.073135400        1         0       0         0  
1     2023-06-16 15:39:54.073135400        1         0       0         0  
2     2023-06-16 15:39:55.073135400        1         0       0         0  
3     2023-06-16 15:39:56.073135400        1         0       0         0  
4     2023-06-16 15:39:57.073135400        1         0       0         0  
...                             ...      ...       ...     ...       ...  
3540  2023-06-16 16:38:53.073135400        0         0       0         1  
3541  2023-06-16 16:38:54.073135400        0         0       0         1  
3542  2023-06-16 16:38:55.073135400        0         0       0         1  
3543  2023-06-16 16:38:56.073135400        0         0       0         1  
3544  2023-06-16 16:38:57.073135400        0         0       0         1  

[3545 rows x 26 columns]

## Feature engineering part 1: rolling mean/median/std/max/min/slope

In [16]:
window_sizes = [2, 5, 8]

columns_to_featurize = [
    'accel_z', 'accel_y', 'accel_x',
    'gyro_z', 'gyro_y', 'gyro_x',
    'gravity_z', 'gravity_y', 'gravity_x',
    'ori_qz', 'ori_qy', 'ori_qx', 'ori_qw',
    'magne_z', 'magne_y', 'magne_x',
    'bar_relativeAltitude', 'bar_pressure',
    'gps_altitude', 'gps_latitude', 'gps_longitude'
]

# Exclude time and label columns
for column in dataset[columns_to_featurize]:
    for window_size in window_sizes:
        rolling_mean = dataset[column].rolling(window_size).mean()
        rolling_median = dataset[column].rolling(window_size).median()
        rolling_std = dataset[column].rolling(window_size).std()
        rolling_max = dataset[column].rolling(window_size).max()
        rolling_min = dataset[column].rolling(window_size).min()

        new_column_mean_name = f"{column}_rolling_mean_{window_size}"
        new_column_median_name = f"{column}_rolling_median_{window_size}"
        new_column_std_name = f"{column}_rolling_std_{window_size}"
        new_column_max_name = f"{column}_rolling_max_{window_size}"
        new_column_min_name = f"{column}_rolling_min_{window_size}"

        dataset[new_column_mean_name] = rolling_mean
        dataset[new_column_median_name] = rolling_median
        dataset[new_column_std_name] = rolling_std
        dataset[new_column_max_name] = rolling_max
        dataset[new_column_min_name] = rolling_min

dataset

/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/1336651659.py:30: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[new_column_std_name] = rolling_std
/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/1336651659.py:31: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  dataset[new_column_max_name] = rolling_max
/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/1336651659.py:32: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` m

accel_z   accel_y   accel_x    gyro_z    gyro_y    gyro_x  gravity_z  \
0    -0.023840  0.018390  0.008858 -0.054503 -0.005479  0.011691  -7.563114   
1     0.002951  0.022089 -0.041490 -0.070068  0.088273 -0.000520  -7.004715   
2     0.083199 -0.117540  0.250466  0.099236 -0.050622 -0.041580  -7.546371   
3    -0.024142 -0.041310 -0.124078  0.268303  0.292325  0.254841  -7.262949   
4    -0.343633  0.325876  0.097991 -0.121707 -0.284418 -0.060837  -6.545389   
...        ...       ...       ...       ...       ...       ...        ...   
3540 -0.027468 -0.002052 -0.012776  0.062467  0.000044 -0.000010  -9.806233   
3541 -0.029051  0.008580  0.018632  0.031754 -0.000316 -0.000033  -9.806149   
3542 -0.028269  0.002606  0.002662 -0.000234 -0.000159  0.000208  -9.806189   
3543 -0.028832  0.002296  0.002630  0.023920  0.000002 -0.000178  -9.806191   
3544 -0.028814  0.002313 -0.000165 -0.000034 -0.000017  0.000023  -9.806191   

      gravity_y  gravity_x    ori_qz  ...  gps_longitude_rolling_mean_5  \
0     -5.831582  -2.216261  0.663099  ...                           NaN   
1     -6.675822  -1.343320  0.653123  ...                           NaN   
2     -6.011996  -1.740925  0.642579  ...                           NaN   
3     -6.160909  -2.257083  0.731410  ...                           NaN   
4     -6.867339  -2.387059  0.749090  ...                      4.382955   
...         ...        ...       ...  ...                           ...   
3540   0.083322   0.035022 -0.157359  ...                      4.384527   
3541   0.079065   0.040456 -0.117536  ...                      4.384527   
3542   0.082902   0.039185 -0.113216  ...                      4.384527   
3543   0.083961   0.039061 -0.108622  ...                      4.384527   
3544   0.083584   0.041470 -0.098873  ...                      4.384527   

      gps_longitude_rolling_median_5  gps_longitude_rolling_std_5  \
0                                NaN                          NaN   
1                                NaN                          NaN   
2                                NaN                          NaN   
3                                NaN                          NaN   
4                           4.382956                 5.360602e-07   
...                              ...                          ...   
3540                        4.384527                 0.000000e+00   
3541                        4.384527                 0.000000e+00   
3542                        4.384527                 0.000000e+00   
3543                        4.384527                 0.000000e+00   
3544                        4.384527                 0.000000e+00   

      gps_longitude_rolling_max_5  gps_longitude_rolling_min_5  \
0                             NaN                          NaN   
1                             NaN                          NaN   
2                             NaN                          NaN   
3                             NaN                          NaN   
4                        4.382956                     4.382954   
...                           ...                          ...   
3540                     4.384527                     4.384527   
3541                     4.384527                     4.384527   
3542                     4.384527                     4.384527   
3543                     4.384527                     4.384527   
3544                     4.384527                     4.384527   

      gps_longitude_rolling_mean_8  gps_longitude_rolling_median_8  \
0                              NaN                             NaN   
1                              NaN                             NaN   
2                              NaN                             NaN   
3                              NaN                             NaN   
4                              NaN                             NaN   
...                            ...                             ...   
3540                      4.384527           

In [17]:
dataset = dataset.drop(dataset.index[0:7])

In [30]:
dataset.columns[]

Index(['accel_z', 'accel_y', 'accel_x', 'gyro_z', 'gyro_y', 'gyro_x',
       'gravity_z', 'gravity_y', 'gravity_x', 'ori_qz',
       ...
       'gps_longitude_rolling_mean_5', 'gps_longitude_rolling_median_5',
       'gps_longitude_rolling_std_5', 'gps_longitude_rolling_max_5',
       'gps_longitude_rolling_min_5', 'gps_longitude_rolling_mean_8',
       'gps_longitude_rolling_median_8', 'gps_longitude_rolling_std_8',
       'gps_longitude_rolling_max_8', 'gps_longitude_rolling_min_8'],
      dtype='object', length=341)

In [18]:
dataset.columns[22:26]

Index(['walking', 'relaxing', 'eating', 'studying'], dtype='object')

In [31]:
from book.Chapter7.FeatureSelection import FeatureSelectionClassification

selection = []

groups = [[26, 41],
 [41, 56],
 [56, 71],
 [71, 86],
 [86, 101],
 [101, 116],
 [116, 131],
 [131, 146],
 [146, 161],
 [161, 176],
 [176, 191],
 [191, 206],
 [206, 221],
 [221, 236],
 [236, 251],
 [251, 266],
 [266, 281],
 [281, 296],
 [296, 311],
 [311, 326],
 [326, 341]]

for x in groups:
    cols = dataset.columns[x[0]:x[1]]
    print(cols)

    X_train, X_test, y_train, y_test = train_test_split(dataset[cols], dataset[['walking', 'relaxing', 'eating', 'studying']].idxmax(axis=1), test_size=0.2, random_state=42)
    forward_select = FeatureSelectionClassification().forward_selection(15, X_train, X_test, y_train, y_test,True)
    selection.append(forward_select)


Index(['accel_z_rolling_mean_2', 'accel_z_rolling_median_2',
       'accel_z_rolling_std_2', 'accel_z_rolling_max_2',
       'accel_z_rolling_min_2', 'accel_z_rolling_mean_5',
       'accel_z_rolling_median_5', 'accel_z_rolling_std_5',
       'accel_z_rolling_max_5', 'accel_z_rolling_min_5',
       'accel_z_rolling_mean_8', 'accel_z_rolling_median_8',
       'accel_z_rolling_std_8', 'accel_z_rolling_max_8',
       'accel_z_rolling_min_8'],
      dtype='object')
Added feature0
Added feature1
Added feature2
Added feature3
Added feature4
Added feature5
Added feature6
Added feature7
Added feature8
Added feature9
Added feature10
Added feature11
Added feature12
Added feature13
Added feature14
Index(['accel_y_rolling_mean_2', 'accel_y_rolling_median_2',
       'accel_y_rolling_std_2', 'accel_y_rolling_max_2',
       'accel_y_rolling_min_2', 'accel_y_rolling_mean_5',
       'accel_y_rolling_median_5', 'accel_y_rolling_std_5',
       'accel_y_rolling_max_5', 'accel_y_rolling_min_5',
       'acc

In [65]:
selection[20][1]


['gps_longitude_rolling_median_8',
 'gps_longitude_rolling_std_2',
 'gps_longitude_rolling_median_5',
 'gps_longitude_rolling_mean_5',
 'gps_longitude_rolling_min_2',
 'gps_longitude_rolling_max_5',
 'gps_longitude_rolling_max_2',
 'gps_longitude_rolling_min_8',
 'gps_longitude_rolling_mean_8',
 'gps_longitude_rolling_min_5',
 'gps_longitude_rolling_median_2',
 'gps_longitude_rolling_mean_2',
 'gps_longitude_rolling_std_5',
 'gps_longitude_rolling_std_8',
 'gps_longitude_rolling_max_8']

In [107]:
to_keep = ['accel_z_rolling_median_8',
 'accel_z_rolling_max_8',
 'accel_z_rolling_min_8',
 'accel_z_rolling_std_2','accel_y_rolling_mean_2',
 'accel_y_rolling_std_2','accel_y_rolling_max_8',
 'accel_y_rolling_std_8',
 'accel_y_rolling_median_8',
 'accel_y_rolling_min_8','accel_x_rolling_min_8',
 'accel_x_rolling_mean_5',
 'accel_x_rolling_min_2',
 'accel_x_rolling_std_2',
 'accel_x_rolling_max_2','gyro_z_rolling_std_8',
 'gyro_z_rolling_max_8','gyro_z_rolling_min_2','gyro_z_rolling_median_2','gyro_y_rolling_std_8',
 'gyro_y_rolling_min_8', 'gyro_y_rolling_max_5','gyro_y_rolling_median_2','gyro_x_rolling_std_8',
 'gyro_x_rolling_min_8',
 'gyro_x_rolling_max_2',
 'gyro_x_rolling_mean_5','gravity_z_rolling_max_8',
 'gravity_z_rolling_min_8',
 'gravity_z_rolling_median_5','gravity_z_rolling_std_5','gravity_y_rolling_median_8',
 'gravity_y_rolling_min_2',
 'gravity_y_rolling_max_2','gravity_y_rolling_std_2','gravity_x_rolling_min_8',
 'gravity_x_rolling_max_5',
 'gravity_x_rolling_mean_5','gravity_x_rolling_std_8','ori_qz_rolling_min_5',
 'ori_qz_rolling_mean_2','ori_qz_rolling_max_2','ori_qz_rolling_std_2','ori_qy_rolling_median_5',
 'ori_qy_rolling_max_5','ori_qy_rolling_min_2','ori_qy_rolling_std_8','ori_qx_rolling_min_8',
 'ori_qx_rolling_median_8','ori_qx_rolling_max_2','ori_qx_rolling_std_8','ori_qw_rolling_max_8',
 'ori_qw_rolling_min_8','ori_qw_rolling_median_5','ori_qw_rolling_std_8','magne_z_rolling_min_8',
 'magne_z_rolling_median_8','magne_z_rolling_max_2','magne_z_rolling_std_5','magne_y_rolling_median_5','magne_y_rolling_max_8',
 'magne_y_rolling_min_8','magne_y_rolling_std_8','magne_x_rolling_max_8',
 'magne_x_rolling_std_8','magne_x_rolling_min_8',
 'magne_x_rolling_mean_8','bar_relativeAltitude_rolling_median_8',
 'bar_relativeAltitude_rolling_std_8','bar_relativeAltitude_rolling_max_5',
 'bar_relativeAltitude_rolling_min_2','bar_pressure_rolling_median_8',
 'bar_pressure_rolling_std_8','bar_pressure_rolling_max_2','bar_pressure_rolling_min_2','gps_altitude_rolling_std_8',
 'gps_altitude_rolling_median_5',
 'gps_altitude_rolling_max_8','gps_altitude_rolling_min_2','gps_latitude_rolling_median_2',
 'gps_latitude_rolling_max_8', 'gps_latitude_rolling_min_2', 'gps_latitude_rolling_std_2','gps_longitude_rolling_median_8',
 'gps_longitude_rolling_std_2','gps_longitude_rolling_min_2',
 'gps_longitude_rolling_max_5',]

In [108]:
to_keep += dataset.columns[:26].tolist()
dataset = dataset[to_keep]

## PCA

accel_z   accel_y   accel_x    gyro_z    gyro_y    gyro_x  gravity_z  \
0    -0.023840  0.018390  0.008858 -0.054503 -0.005479  0.011691  -7.563114   
1     0.002951  0.022089 -0.041490 -0.070068  0.088273 -0.000520  -7.004715   
2     0.083199 -0.117540  0.250466  0.099236 -0.050622 -0.041580  -7.546371   
3    -0.024142 -0.041310 -0.124078  0.268303  0.292325  0.254841  -7.262949   
4    -0.343633  0.325876  0.097991 -0.121707 -0.284418 -0.060837  -6.545389   
...        ...       ...       ...       ...       ...       ...        ...   
3540 -0.027468 -0.002052 -0.012776  0.062467  0.000044 -0.000010  -9.806233   
3541 -0.029051  0.008580  0.018632  0.031754 -0.000316 -0.000033  -9.806149   
3542 -0.028269  0.002606  0.002662 -0.000234 -0.000159  0.000208  -9.806189   
3543 -0.028832  0.002296  0.002630  0.023920  0.000002 -0.000178  -9.806191   
3544 -0.028814  0.002313 -0.000165 -0.000034 -0.000017  0.000023  -9.806191   

      gravity_y  gravity_x    ori_qz  ...    pca_12    pca_13    pca_14  \
0     -5.831582  -2.216261  0.663099  ... -0.010103  0.027760 -0.018532   
1     -6.675822  -1.343320  0.653123  ...  0.008352  0.032153 -0.061326   
2     -6.011996  -1.740925  0.642579  ... -0.092605  0.096222 -0.015881   
3     -6.160909  -2.257083  0.731410  ... -0.107571 -0.140638 -0.255344   
4     -6.867339  -2.387059  0.749090  ...  0.089057  0.037180  0.149664   
...         ...        ...       ...  ...       ...       ...       ...   
3540   0.083322   0.035022 -0.157359  ... -0.005713 -0.019440  0.005114   
3541   0.079065   0.040456 -0.117536  ... -0.010504 -0.018953  0.013085   
3542   0.082902   0.039185 -0.113216  ... -0.006161 -0.012409  0.011700   
3543   0.083961   0.039061 -0.108622  ... -0.007025 -0.017162  0.010308   
3544   0.083584   0.041470 -0.098873  ... -0.005788 -0.012912  0.011330   

        pca_15    pca_16    pca_17    pca_18    pca_19    pca_20    pca_21  
0    -0.017443 -0.046898  0.031689  0.063796  0.131823  0.002484 -0.014856  
1    -0.021201  0.000380  0.043054  0.049280  0.129422  0.011905 -0.008786  
2     0.062878 -0.063570 -0.006964  0.138489  0.121110 -0.016193 -0.022343  
3    -0.003400 -0.004964 -0.080230  0.054262  0.113783 -0.001250 -0.025104  
4    -0.085108 -0.073065  0.064698  0.154808  0.130672  0.011380  0.002727  
...        ...       ...       ...       ...       ...       ...       ...  
3540  0.004124 -0.009706 -0.031207 -0.002569  0.001509  0.001316  0.016968  
3541  0.001474 -0.010792 -0.006504  0.001604  0.005187  0.001775 -0.024875  
3542 -0.004962 -0.006347  0.003179 -0.003190  0.004852  0.000989 -0.023785  
3543 -0.002687 -0.009410 -0.007179 -0.000638  0.006287  0.000851 -0.018241  
3544 -0.005824 -0.007231  0.002183 -0.003496  0.005775  0.001028 -0.017328  

[3545 rows x 362 columns]

## Fourier

In [109]:
import numpy as np

window_sizes = [30]
num_fourier_features = 5

columns_to_featurize = [
    'accel_z', 'accel_y', 'accel_x',
    'gyro_z', 'gyro_y', 'gyro_x',
    'gravity_z', 'gravity_y', 'gravity_x',
    'ori_qz', 'ori_qy', 'ori_qx', 'ori_qw',
    'magne_z', 'magne_y', 'magne_x',
    'bar_relativeAltitude', 'bar_pressure',
    'gps_altitude', 'gps_latitude', 'gps_longitude'
]

# Exclude time and label columns
for column in dataset[columns_to_featurize]:
    for window_size in window_sizes:
        rolling_mean = dataset[column].rolling(window_size).mean().fillna(0)
        new_column_mean_name = f"{column}_rolling_mean_{window_size}"
        dataset[new_column_mean_name] = rolling_mean
        
        data = rolling_mean.values
        
        # Compute FFT
        fft_result = np.fft.fft(data)
        
        # Mean Power Spectrum
        power_spectrum = np.abs(fft_result) ** 2
        new_column_power_name = f"{column}_power_window_{window_size}"
        dataset[new_column_power_name] = power_spectrum.mean()
        
        # Mean Amplitude Spectrum
        amplitude_spectrum = np.abs(fft_result)
        new_column_amplitude_name = f"{column}_amplitude_window_{window_size}"
        dataset[new_column_amplitude_name] = amplitude_spectrum.mean()
        
        # Total Power or Energy
        total_power = np.sum(power_spectrum)
        new_column_energy_name = f"{column}_total_power_{window_size}"
        dataset[new_column_energy_name] = total_power
        
        # Mean Frequency
        frequencies = np.fft.fftfreq(len(data))
        mean_frequency = np.sum(power_spectrum * frequencies) / total_power
        new_column_mean_freq_name = f"{column}_mean_frequency_{window_size}"
        dataset[new_column_mean_freq_name] = mean_frequency
dataset

/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/3769537876.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset[new_column_mean_name] = rolling_mean
/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/3769537876.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset[new_column_power_name] = power_spectrum.mean()
/var/folders/_6/3cydh_512s94j8m3t47xggm00000gn/T/ipykernel_41839/3769537876.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a sli

accel_z_rolling_median_8  accel_z_rolling_max_8  accel_z_rolling_min_8  \
7                    -0.021895               0.308984              -0.343633   
8                    -0.008500               0.349426              -0.343633   
9                     0.031624               0.349426              -0.343633   
10                   -0.022046               0.349426              -0.613662   
11                   -0.104185               0.349426              -0.613662   
...                        ...                    ...                    ...   
3540                 -0.029285              -0.027468              -0.029963   
3541                 -0.029285              -0.027468              -0.029963   
3542                 -0.029285              -0.027468              -0.029963   
3543                 -0.029116              -0.027468              -0.029963   
3544                 -0.028942              -0.027468              -0.029963   

      accel_z_rolling_std_2  accel_y_rolling_mean_2  accel_y_rolling_std_2  \
7                  0.351717               -0.594376               0.201246   
8                  0.380314               -0.197819               0.762063   
9                  0.158875                0.238945               0.144386   
10                 0.522132                0.279815               0.202185   
11                 0.193744                0.362771               0.084868   
...                     ...                     ...                    ...   
3540               0.001211                0.001268               0.004695   
3541               0.001119                0.003264               0.007518   
3542               0.000553                0.005593               0.004225   
3543               0.000399                0.002451               0.000219   
3544               0.000013                0.002305               0.000012   

      accel_y_rolling_max_8  accel_y_rolling_std_8  accel_y_rolling_median_8  \
7                  0.325876               0.331277                 -0.011460   
8                  0.341041               0.367468                 -0.009610   
9                  0.341041               0.373957                  0.010884   
10                 0.422782               0.409230                  0.099964   
11                 0.422782               0.421277                  0.219805   
...                     ...                    ...                       ...   
3540               0.006000               0.002440                  0.004450   
3541               0.008580               0.002994                  0.004595   
3542               0.008580               0.003046                  0.004450   
3543               0.008580               0.003105                  0.004450   
3544               0.008580               0.003147                  0.003597   

      accel_y_rolling_min_8  ...  gps_latitude_rolling_mean_30  \
7                 -0.736679  ...                      0.000000   
8                 -0.736679  ...                      0.000000   
9                 -0.736679  ...                      0.000000   
10                -0.736679  ...                      0.000000   
11                -0.736679  ...                      0.000000   
...                     ...  ...                           ...   
3540              -0.002052  ...                     52.045305   
3541              -0.002052  ...                     52.045305   
3542              -0.002052  ...                     52.045305   
3543              -0.002052  ...                     52.045305   
3544              -0.002052  ...                     52.045305   

      gps_latitude_power_window_30  gps_latitude_amplitude_window_30  \
7                     9.504928e+06                        173.712894   
8                     9.504928e+06                        173.712894   
9                     9.504928e+06                        173.712894   
10                    9.504928e+06                        173.7128

In [126]:
x = dataset.drop(columns=['walking', 'relaxing', 'eating', 'studying','time'])

X_train, X_test, y_train, y_test = train_test_split(x, dataset[['walking', 'relaxing', 'eating', 'studying']].idxmax(axis=1), test_size=0.2, random_state=42)


forward_select = FeatureSelectionClassification().forward_selection(150, X_train, X_test, y_train, y_test,True)

Added feature0
Added feature1
Added feature2
Added feature3
Added feature4
Added feature5
Added feature6
Added feature7
Added feature8
Added feature9
Added feature10
Added feature11
Added feature12
Added feature13
Added feature14
Added feature15
Added feature16
Added feature17
Added feature18
Added feature19
Added feature20
Added feature21
Added feature22
Added feature23
Added feature24
Added feature25
Added feature26
Added feature27
Added feature28
Added feature29
Added feature30
Added feature31
Added feature32
Added feature33
Added feature34
Added feature35
Added feature36
Added feature37
Added feature38
Added feature39
Added feature40
Added feature41
Added feature42
Added feature43
Added feature44
Added feature45
Added feature46
Added feature47
Added feature48
Added feature49
Added feature50
Added feature51
Added feature52
Added feature53
Added feature54
Added feature55
Added feature56
Added feature57
Added feature58
Added feature59
Added feature60
Added feature61
Added feature62
Ad

In [130]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

# Assuming your dataset is stored in a DataFrame called 'df'

# Calculate the correlation matrix
correlation_matrix = dataset.corr()

# Create a heatmap
plt.figure(figsize=(150, 120))
sns.heatmap(correlation_matrix, annot=True, cmap="coolwarm")


<AxesSubplot:>

In [133]:
import pandas as pd

# Assuming your dataset is stored in a DataFrame called 'df'

# Calculate the correlation matrix
correlation_matrix = dataset.corr()

# Set a threshold for the correlation coefficient
threshold = 0.9  # Adjust as needed

# Create an empty list to store the collinear features
collinear_features = []

# Iterate through the correlation matrix and find collinear features
for i in range(len(correlation_matrix.columns)):
    for j in range(i+1, len(correlation_matrix.columns)):
        if abs(correlation_matrix.iloc[i, j]) > threshold:
            # Add the collinear features to the list
            feature_i = correlation_matrix.columns[i]
            feature_j = correlation_matrix.columns[j]
            collinear_features.append((feature_i, feature_j))

# Print the list of collinear features
for feature_pair in collinear_features:
    print(f"Collinear Features: {feature_pair[0]} and {feature_pair[1]}")

Collinear Features: accel_y_rolling_max_8 and accel_y_rolling_std_8
Collinear Features: gyro_y_rolling_std_8 and gyro_y_rolling_min_8
Collinear Features: gyro_x_rolling_std_8 and gyro_x_rolling_min_8
Collinear Features: gravity_z_rolling_max_8 and gravity_z_rolling_min_8
Collinear Features: gravity_z_rolling_max_8 and gravity_z_rolling_median_5
Collinear Features: gravity_z_rolling_max_8 and ori_qx_rolling_min_8
Collinear Features: gravity_z_rolling_max_8 and gravity_z
Collinear Features: gravity_z_rolling_max_8 and gravity_z_rolling_mean_30
Collinear Features: gravity_z_rolling_min_8 and gravity_z_rolling_median_5
Collinear Features: gravity_z_rolling_min_8 and ori_qx_rolling_median_8
Collinear Features: gravity_z_rolling_min_8 and ori_qx_rolling_max_2
Collinear Features: gravity_z_rolling_min_8 and magne_z_rolling_min_8
Collinear Features: gravity_z_rolling_min_8 and magne_z_rolling_median_8
Collinear Features: gravity_z_rolling_min_8 and magne_z_rolling_max_2
Collinear Features: gra

In [134]:
len(collinear_features)

201

In [ ]:
from book.Chapter3.DataTransformation import PrincipalComponentAnalysis

dataset = PrincipalComponentAnalysis().apply_pca(dataset, columns_to_featurize, len(columns_to_featurize))
dataset

## Saving experiment state

In [29]:
from pathlib import Path

# saving the state for faster further experimentation
target_directory = "final_datasets"
Path(target_directory).mkdir(exist_ok=True, parents=True)
dataset.to_csv(f"{target_directory}/{EXPERIMENT}_{MODE}_features.csv", index=False)